<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Features-Engeneering-and-Selection" data-toc-modified-id="Features-Engeneering-and-Selection-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Features Engeneering and Selection</a></span><ul class="toc-item"><li><span><a href="#Split-the-Data" data-toc-modified-id="Split-the-Data-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Split the Data</a></span><ul class="toc-item"><li><span><a href="#Target-Encoding" data-toc-modified-id="Target-Encoding-1.1.1"><span class="toc-item-num">1.1.1&nbsp;&nbsp;</span>Target Encoding</a></span></li></ul></li></ul></li><li><span><a href="#Modeling" data-toc-modified-id="Modeling-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Modeling</a></span><ul class="toc-item"><li><span><a href="#Models-For-Regression" data-toc-modified-id="Models-For-Regression-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Models For Regression</a></span><ul class="toc-item"><li><span><a href="#Linear-Models" data-toc-modified-id="Linear-Models-2.1.1"><span class="toc-item-num">2.1.1&nbsp;&nbsp;</span>Linear Models</a></span></li><li><span><a href="#Tree-Based-Model" data-toc-modified-id="Tree-Based-Model-2.1.2"><span class="toc-item-num">2.1.2&nbsp;&nbsp;</span>Tree Based Model</a></span></li><li><span><a href="#Ensemble-Models" data-toc-modified-id="Ensemble-Models-2.1.3"><span class="toc-item-num">2.1.3&nbsp;&nbsp;</span>Ensemble Models</a></span></li><li><span><a href="#Tuninig-Lgb-model" data-toc-modified-id="Tuninig-Lgb-model-2.1.4"><span class="toc-item-num">2.1.4&nbsp;&nbsp;</span>Tuninig Lgb model</a></span></li></ul></li><li><span><a href="#Preprocessing" data-toc-modified-id="Preprocessing-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Preprocessing</a></span></li></ul></li></ul></div>

In [48]:
import numpy as np
import pandas as pd
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt


pd.plotting.register_matplotlib_converters()
%matplotlib inline
from IPython.display import display
from itertools import combinations
from collections import Counter


import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor


# pre_preprocessing
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, LabelEncoder , StandardScaler , MinMaxScaler , RobustScaler


# Resampling
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler

# Valdiation
from sklearn.model_selection import StratifiedShuffleSplit , StratifiedKFold , GroupKFold
from sklearn.model_selection import train_test_split,cross_val_score
from sklearn.model_selection import KFold

# Modeling
from sklearn.decomposition import PCA
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.svm import SVR
from xgboost import XGBRegressor
from lightgbm import LGBMRegressor


# Metrics
from sklearn.metrics import r2_score , median_absolute_error , mean_squared_error, mean_absolute_error

import warnings
warnings.filterwarnings('ignore')

#display all column of df 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None) 
# to format the scientific presntastion of numbers 
pd.options.display.float_format = '{:.2f}'.format


# Features Engeneering and Selection

In [49]:
df_clean = pd.read_csv('Clean_data2.csv')

## Split the Data

In [50]:
train , test , y_train , y_test = train_test_split(df_clean.drop('sales',axis=1),df_clean.sales ,
                                                   test_size=0.30, shuffle=True,random_state=45)

In [51]:
train.shape,test.shape

((126021, 21), (54010, 21))

In [52]:
# The delay in orders
for df in [train,test]:
    
    df['DelayOrdered'] = df['days_for_shipment_(scheduled)'] - df['days_for_shipping_(real)']
    df.drop(['days_for_shipment_(scheduled)','days_for_shipping_(real)'], axis=1, inplace=True)



train['DiscountPerProduct'] = train['product_name'].map(dict(train.groupby('product_name')['order_item_discount'].max()))
test['DiscountPerProduct'] = test['product_name'].map(dict(test.groupby('product_name')['order_item_discount'].max()))


train['DenefitPerProduct'] = train['product_name'].map(dict(train.groupby('product_name')['benefit_per_order'].mean()))
test['DenefitPerProduct'] = test['product_name'].map(dict(test.groupby('product_name')['benefit_per_order'].mean()))


train['TotalDiscountPerProduct'] = train['product_name'].map(dict(train.groupby('product_name')['order_item_discount'].var()))
test['TotalDiscountPerProduct'] = test['product_name'].map(dict(test.groupby('product_name')['order_item_discount'].var()))


# Example 2: Compute the standard deviation of discounts per product
train['MaxDiscountPerOrder'] = train['order_item_id'].map(dict(train.groupby('order_item_id')['order_item_discount'].max()))
test['MaxDiscountPerOrder'] = test['order_item_id'].map(dict(test.groupby('order_item_id')['order_item_discount'].max()))

In [53]:
train.drop(['order_item_discount_rate','order_item_profit_ratio'],axis=1,inplace=True)
test.drop(['order_item_discount_rate','order_item_profit_ratio'],axis=1,inplace=True)

In [54]:
train.drop(['product_category_id','customer_id','order_item_id','order_id'],axis=1,inplace=True)
test.drop(['product_category_id','customer_id','order_item_id','order_id'],axis=1,inplace=True)

### Target Encoding

`Target encoding is a feature engineering technique used to handle categorical variables by encoding them based on the target variable. Instead of assigning arbitrary numerical values to categories (like in label encoding) or creating additional features (like in one-hot encoding), target encoding uses the mean of the target variable for each category as the encoded value.`

In [55]:
colms = ['product_name']
from category_encoders import TargetEncoder
Te = TargetEncoder()
for col in colms:
    train[f"{col}_mean"] = Te.fit_transform(train[f"{col}"], y_train)
    test[f"{col}_mean"] = Te.transform(test[f"{col}"])
    
    train.drop(col , axis=1, inplace=True)
    test.drop(col , axis=1, inplace=True)    

In [56]:
train['product_name_mean'].corr(y_train)

0.8377665307298386

In [57]:
cat = train.select_dtypes(include="O").columns.to_list()
num = train.select_dtypes(exclude='O').columns.to_list()

# Modeling

## Models For Regression

### Linear Models

1. Linear Reggression(OLS)
2. Ridge Reggression(L1 norm)
3. Lasso Reggression(L2 norm)
4. Elistic Net

In [58]:
from sklearn.linear_model import LinearRegression, Ridge, Lasso, ElasticNet
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import RobustScaler, OneHotEncoder,PolynomialFeatures
from imblearn.pipeline import Pipeline

Linear_models = {
    
    "Linear Regression" : LinearRegression(),
    "Rideg" : Ridge(),
    "Lasso" : Lasso(),
    "ElasticNet": ElasticNet()
}

Linear_processer = ColumnTransformer(
    
    
    transformers = [ 
    
    
        ('num', Pipeline(steps=[ ('scaler', StandardScaler())]), num),
    
        ('cat',Pipeline(steps=[('one_hot',OneHotEncoder(drop='first'))]),cat)
        
    
                                                                                ])

# Evaluate Each Model
for name, model in Linear_models.items():
    
    # Create Pipeline
    
    pipeline = Pipeline(steps=[
        
        ("preprocessor", Linear_processer),

        ("model", model)
    ])
    
    # Cross-Validation
    scores = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_squared_error")
    
    scores2 = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_absolute_error")
    
    scores3 = cross_val_score(pipeline, train, y_train, cv=5, scoring="r2")
    
    rmse_scores = np.sqrt(-scores)
    
    MAE_scores = np.sqrt(-scores2)
    
    R2_score = np.mean(scores3)
    

    print(f"Model: {name}")
    print(f"Cross-Validation RMSE: {rmse_scores.mean():.2f} (+/- {rmse_scores.std():.2f})")
    
    print(f"Cross-Validation MAE: {MAE_scores.mean():.2f} (+/- {MAE_scores.std():.2f})")
    
    print(f"Cross-Validation R2_score : {R2_score:.3f}\n")

Model: Linear Regression
Cross-Validation RMSE: 27.92 (+/- 0.17)
Cross-Validation MAE: 4.39 (+/- 0.01)
Cross-Validation R2_score : 0.940

Model: Rideg
Cross-Validation RMSE: 27.92 (+/- 0.17)
Cross-Validation MAE: 4.39 (+/- 0.01)
Cross-Validation R2_score : 0.940

Model: Lasso
Cross-Validation RMSE: 28.16 (+/- 0.16)
Cross-Validation MAE: 4.41 (+/- 0.01)
Cross-Validation R2_score : 0.939

Model: ElasticNet
Cross-Validation RMSE: 44.38 (+/- 0.16)
Cross-Validation MAE: 5.75 (+/- 0.01)
Cross-Validation R2_score : 0.850



### Tree Based Model

1. Decision Tree
2. Gradint Boosting  
3. Extra Trees


        I's Known that most of the tree models were likely to overfit without any tunnig so here we adjust some parameters for meaningful results

In [59]:
from sklearn.ensemble import RandomForestRegressor,HistGradientBoostingRegressor,StackingRegressor,ExtraTreesRegressor
# from xgboost import XGBRegressor
# from lightgbm import LGBMRegressor
from sklearn.tree import DecisionTreeRegressor


tree_models = {
    
    "LightGBM": LGBMRegressor(n_estimators = 200, random_state = 45, learning_rate = 0.01 ),
    
    "Decision Tree": DecisionTreeRegressor(random_state=45,max_depth=5)
    
}

tree_processer = ColumnTransformer(transformers=[
    
    
        ('num', Pipeline(steps=[ ('scaler', StandardScaler())]), num),
    
        ('cat',Pipeline(steps=[('one_hot',OneHotEncoder(drop='first'))]),cat) ])

# Evaluate Each Model
for name, model in tree_models.items():
    
    # Create Pipeline
    pipeline = Pipeline(steps=[
        
        ("Processre" , tree_processer ),
                
        ("model", model)
    ])
    
    # Cross-Validation
    scores = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_squared_error")
    
    scores2 = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_absolute_error")
    
    scores3 = cross_val_score(pipeline, train, y_train, cv=5, scoring="r2")
    
    rmse_scores = np.sqrt(-scores)
    
    MAE_scores = np.sqrt(-scores2)
    
    R2_score = np.mean(scores3)
    

    print(f"Model: {name}")
    print(f"Cross-Validation RMSE: {rmse_scores.mean():.2f} (+/- {rmse_scores.std():.2f})")
    print(f"Cross-Validation MAE: {MAE_scores.mean():.2f} (+/- {MAE_scores.std():.2f})")
    print(f"Cross-Validation R2_score : {R2_score:.3f}\n")

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011423 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1288
[LightGBM] [Info] Number of data points in the train set: 100816, number of used features: 28
[LightGBM] [Info] Start training from score 200.341686
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005868 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1288
[LightGBM] [Info] Number of data points in the train set: 100817, number of used features: 28
[LightGBM] [Info] Start training from score 200.463444
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.012794 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not

### Ensemble Models

1. Stacking

In [33]:
from sklearn.ensemble import RandomForestRegressor,HistGradientBoostingRegressor,StackingRegressor
from sklearn.svm import SVR


estimators = [
    
    ('lr', LinearRegression()),
    ('lgbm',  DecisionTreeRegressor(random_state=45,max_depth=5))]

StackModels = StackingRegressor(
    
    estimators=estimators,
    
    final_estimator= Lasso() 
)

pipeline = Pipeline(steps=[
    
    ('preprocessor', tree_processer),
    
    ("Model", StackModels)
])


# Cross-Validation
scores = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_squared_error")
    
scores2 = cross_val_score(pipeline, train, y_train, cv=5, scoring="neg_mean_absolute_error")
    
scores3 = cross_val_score(pipeline, train, y_train, cv=5, scoring="r2")
    
rmse_scores = np.sqrt(-scores)
    
MAE_scores = np.sqrt(-scores2)
    
R2_score = np.mean(scores3)
    

print(f"Model: StackModels")
print(f"Cross-Validation RMSE: {rmse_scores.mean():.2f} (+/- {rmse_scores.std():.2f})")
print(f"Cross-Validation MAE: {MAE_scores.mean():.2f} (+/- {MAE_scores.std():.2f})")
print(f"Cross-Validation R2_score : {R2_score:.3f}\n")

Model: Decision Tree
Cross-Validation RMSE: 15.25 (+/- 0.14)
Cross-Validation MAE: 3.36 (+/- 0.01)
Cross-Validation R2_score : 0.982



**The above Resultes shows that the problem could have different solutions. Alought we gonna choose the LIGHT GBM Model since it's fast and good with momery and deployed**

### Tuninig Lgb model

In [34]:
from sklearn.model_selection import GridSearchCV  
import lightgbm as lgb

In [63]:
# Set up LightGBM regressor
lgbm = lgb.LGBMRegressor(random_state=42)

In [62]:
X_train = tree_processer.fit_transform(train)

In [67]:
# Define parameter grid
param_grid = {
    
    'learning_rate': [0.01, 0.05, 0.01],
    'num_leaves': [100, 80, 70],
    'max_depth':  [4,5,7],
    "num_iterations" : [100,200,300,1000],
    'min_data_in_leaf': [20, 50, 100],
    'feature_fraction': [0.8, 0.9, 1.0],
    'bagging_fraction': [0.5, 0.7, 0.9],
    "max_bin": [50,100,200]
}



# # Grid search with cross-validation
# grid_search = GridSearchCV(lgbm, param_grid, scoring='neg_root_mean_squared_error', cv=5)
# grid_search.fit(X_train, y_train)

# # Best parameters
# print("Best parameters found: ", grid_search.best_params_)

from sklearn.model_selection import RandomizedSearchCV

# Random search
random_search = RandomizedSearchCV( estimator=lgbm, param_distributions=param_grid,n_iter=50, cv=3, 
                                   scoring='neg_root_mean_squared_error',random_state=42)

random_search.fit(X_train, y_train)

print("Best parameters:", random_search.best_params_)

[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] feature_fraction is set=0.9, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9
[LightGBM] [Warning] bagging_fraction is set=0.9, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004533 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 792
[LightGBM] 

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] feature_fraction is set=1.0, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=1.0
[LightGBM] [Warning] bagging_fraction is set=0.7, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7
[LightGBM] [Warning] min_data_in_leaf is set=20, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=20
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006082 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 794
[LightGBM] [Info] Number of data points in the train set: 126021, number of used features: 28
[LightGBM] [Info] Start training from score 200.389920
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[Lig

In [68]:
random_search.best_score_

-0.23145127051969536

In [69]:
from sklearn.experimental import enable_halving_search_cv
from sklearn.model_selection import HalvingRandomSearchCV

# Define the parameter space
param_dist = {
    'learning_rate': [0.01, 0.05, 0.1, 0.2],
    'num_leaves': [15, 31, 63],
    'max_depth': [1, 5, 10],
    'min_child_samples': [10, 20, 50],
    'subsample': [0.6, 0.8, 1.0],
    'colsample_bytree': [0.6, 0.8, 1.0],
    'n_estimators': [100, 200, 300]
}

# Set up HalvingRandomSearchCV
halving_search = HalvingRandomSearchCV(
    estimator=Model,
    param_distributions=param_dist,
    factor=2,  # Halving factor
    max_resources=200,  # Maximum number of estimators to test
    random_state=42,
    scoring='r2',  # Evaluation metric
    cv=5,  # 5-fold cross-validation
    verbose=1,  # Display progress
    n_jobs=-1  # Parallelize
)


# Perform the search
halving_search.fit(X_train, y_train)

# Display the best parameters
print("Best Parameters:", halving_search.best_params_)
print("Best score:", halving_search.best_score_)

n_iterations: 5
n_required_iterations: 5
n_possible_iterations: 5
min_resources_: 10
max_resources_: 200
aggressive_elimination: False
factor: 2
----------
iter: 0
n_candidates: 20
n_resources: 10
Fitting 5 folds for each of 20 candidates, totalling 100 fits
[LightGBM] [Warning] There are no meaningful features which satisfy the provided configuration. Decreasing Dataset parameters min_data_in_bin or min_data_in_leaf and re-constructing Dataset might resolve this warning.
[LightGBM] [Info] Total Bins 0
[LightGBM] [Info] Number of data points in the train set: 8, number of used features: 0
[LightGBM] [Info] Start training from score 241.306252
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training

/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more 

/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_regression.py:1187: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  war

[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more 

...

[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more 

----------
iter: 4
n_candidates: 2
n_resources: 160
Fitting 5 folds for each of 2 candidates, totalling 10 fits
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are no more leaves that meet the split requirements
[LightGBM] [Warning] Stopped training because there are 

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.008078 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1290
[LightGBM] [Info] Number of data points in the train set: 126021, number of used features: 28
[LightGBM] [Info] Start training from score 200.389920
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best ga

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f